In [1]:
from pathlib import Path

In [174]:
from markdownify import markdownify as md
from pprint import pprint
from html2text import HTML2Text
import re
handler = HTML2Text()

for file in Path("data/raw").iterdir():
    with open(file, "rt", encoding="ISO-8859-2") as f:
        content = f.read()

    content = content.replace("</BLOCKQUOTE>", "").replace("<BLOCKQUOTE>", "")
    text = handler.handle(content)

    pat = re.compile(r"\*\*\s*?(.*?)\s*?\*\*", flags=re.DOTALL)

    def replace(match):
        replacement = match.group(1).replace("\n", "")
        return f'**{replacement}**'
    
    text = pat.sub(replace, text)

    with open(f"data/parsed/{file.stem}.md", "wt") as f:
        f.write(text)

In [230]:
from markdownify import markdownify as md
from pprint import pprint
import json
from html2text import HTML2Text
handler = HTML2Text()

def get_file_name(title):
    return title.lower().replace(" ", "_").replace(".", "_").replace(",", "_")


def split_articles(content):
    split = re.split("\*\*Art\. (\d+).*\*\*", content)
    split = [s.strip() for s in split if s.strip()]
    return dict(zip(split[::2], split[1::2]))

chapter_titles = {}
for file in Path("data/parsed").iterdir():

    with open(file, "rt") as f:
        content = f.read().strip()

    headings = re.findall(r'\*\*(?!Art\.)(.*?)\*\*\s*', content)
    if headings[0] == "Rozdział I":
        headings = [headings[0] + " " + headings[1], *headings[2:]]
    
    chapter_title = re.sub(r'Rozdział .*? ', "", headings[0])
    chapter_titles[file.stem] = chapter_title.strip()
    headings = headings[1:]
    
    split = re.split(r'\*\*(?!Art\.).*?\*\*\s*', content)
    split = [s.strip() for s in split if s.strip()]
    
    if len(headings) < len(split):
        heading = chapter_titles[file.stem]
        headings = [heading, *headings]
    
    Path(f"data/processed/{file.stem}").mkdir(exist_ok=True, parents=True)
    for file_number, (title, file_content) in enumerate(zip(headings, split)):
        file_name = get_file_name(title)

        
        with open(f"data/processed/{file.stem}/{file_number}_{file_name}.md", "wt") as f:
            f.write(file_content)
    
    subheadings = headings
    if headings[0] == chapter_titles[file.stem]:
        subheadings[0] = ""

    meta = {
        "number": file.stem,
        "title": chapter_titles[file.stem],
        "subheadings": headings
    }
    with open(f"data/processed/{file.stem}/meta.json", "wt") as f:
        json.dump(meta, f, ensure_ascii=False, indent=4)
print(chapter_titles)

{'5': 'PREZYDENT RZECZYPOSPOLITEJ POLSKIEJ', '1': 'RZECZPOSPOLITA', '0': 'KONSTYTUCJA  RZECZYPOSPOLITEJ POLSKIEJz dnia 2 kwietnia 1997 r.PREAMBUŁA', '4': 'SEJM I SENAT', '12': 'ZMIANA KONSTYTUCJI', '13': 'PRZEPISY PRZEJŚCIOWE I KOŃCOWE', '10': 'FINANSE PUBLICZNE', '9': 'ORGANY KONTROLI PAŃSTWOWEJ  I OCHRONY PRAWA', '11': 'STANY NADZWYCZAJNE', '8': 'SĄDY I TRYBUNAŁY', '3': 'ŹRÓDŁA PRAWA', '7': 'SAMORZĄD TERYTORIALNY', '6': 'RADA MINISTRÓW I ADMINISTRACJA RZĄDOWA', '2': 'WOLNOŚCI, PRAWA I OBOWIĄZKI CZŁOWIEKA I OBYWATELA'}


In [240]:
with open("data/processed/1/0_rzeczpospolita.md") as f:
    content = f.read()
    split = re.split("\*\*Art\. (\d+).*\*\*", content)
    split = [s.strip() for s in split if s.strip()]
    pprint(dict(zip(split[::2], split[1::2])))

{'1': 'Rzeczpospolita Polska jest dobrem wspólnym wszystkich obywateli.',
 '10': '1. Ustrój Rzeczypospolitej Polskiej opiera się na podziale i '
       'równowadze władzy ustawodawczej, władzy wykonawczej i władzy '
       'sądowniczej.\n'
       '\n'
       '  2. Władzę ustawodawczą sprawują Sejm i Senat, władzę wykonawczą '
       'Prezydent Rzeczypospolitej Polskiej i Rada Ministrów, a władzę '
       'sądowniczą sądy i trybunały.',
 '11': '1. Rzeczpospolita Polska zapewnia wolność tworzenia i działania partii '
       'politycznych. Partie polityczne zrzeszają na zasadach dobrowolności i '
       'równości obywateli polskich w celu wpływania metodami demokratycznymi '
       'na kształtowanie polityki państwa.\n'
       '\n'
       '  2. Finansowanie partii politycznych jest jawne.',
 '12': 'Rzeczpospolita Polska zapewnia wolność tworzenia i działania związków\n'
       'zawodowych, organizacji społeczno-zawodowych rolników, stowarzyszeń, '
       'ruchów\n'
       'obywatelskich, 

In [ ]:
for chapter in Path("data/processed").iterdir():
    print(chapter)
    meta = json.load(open(chapter / "meta.json"))
    chapter_number = meta["number"]
    chapter_title = meta["title"]
    subheadings = meta["subheadings"]
    subchapters = {}
    for file in chapter.glob("*.md"):
        with open(file, "rt") as f:
            number = file.stem.split("_")[0]
            if number not in subchapters:
                subchapters[number] = {}
            f.read()

In [232]:
for chapter in Path("data/processed").iterdir():
    print(chapter)
    meta = json.load(open(chapter / "meta.json"))
    chapter_number = meta["number"]
    chapter_title = meta["title"]
    subheadings = meta["subheadings"]
    subchapters = {}
    for file in chapter.glob("*.md"):
        with open(file, "rt") as f:
            number = file.stem.split("_")[0]
            if number not in subchapters:
                subchapters[number] = {}
            subchapters[number]["content"] = f.read()
            subchapters[number]["heading"] = subheadings[int(number)]

    print(subchapters)
    print(chapter_number, chapter_title)

data/processed/9
{'2': {'content': '**Art. 213.**\n\n  1. Krajowa Rada Radiofonii i Telewizji stoi na straży wolności słowa, prawa do informacji oraz interesu publicznego w radiofonii i telewizji.\n\n  2. Krajowa Rada Radiofonii i Telewizji wydaje rozporządzenia, a w sprawach indywidualnych podejmuje uchwały.\n**Art. 214.**\n\n  1. Członkowie Krajowej Rady Radiofonii i Telewizji są powoływani przez Sejm, Senat i Prezydenta Rzeczypospolitej.\n\n  2. Członek Krajowej Rady Radiofonii i Telewizji nie może należeć do partii politycznej, związku zawodowego ani prowadzić działalności publicznej nie dającej się pogodzić z godnością pełnionej funkcji.\n**Art. 215.**\n\nZasady i tryb działania Krajowej Rady Radiofonii i Telewizji, jej organizację\noraz szczegółowe zasady powoływania jej członków określa ustawa.', 'heading': 'KRAJOWA RADA RADIOFONII I TELEWIZJI'}, '1': {'content': '**Art. 208.**\n\n  1. Rzecznik Praw Obywatelskich stoi na straży wolności i praw człowieka i obywatela określonych w

In [255]:
from markdownify import markdownify as md
from pprint import pprint
import json
from html2text import HTML2Text
handler = HTML2Text()

def get_file_name(title):
    return title.lower().replace(" ", "_").replace(".", "_").replace(",", "_")


def split_articles(content):
    split = re.split("\*\*Art\. (\d+).*\*\*", content)
    split = [s.strip() for s in split if s.strip()]
    if len(split) == 1:
        split = ["-1", split[0]]
    return dict(zip(split[::2]), split[1::2])

chapter_titles = {}
chapters = []
for file in Path("data/parsed").iterdir():

    with open(file, "rt") as f:
        content = f.read().strip()

    headings = re.findall(r'\*\*(?!Art\.)(.*?)\*\*\s*', content)
    if headings[0] == "Rozdział I":
        headings = [headings[0] + " " + headings[1], *headings[2:]]
    
    chapter_title = re.sub(r'Rozdział .*? ', "", headings[0])
    chapter_titles[file.stem] = chapter_title.strip()
    headings = headings[1:]
    
    split = re.split(r'\*\*(?!Art\.).*?\*\*\s*', content)
    split = [s.strip() for s in split if s.strip()]
    
    if len(headings) < len(split):
        heading = chapter_titles[file.stem]
        headings = [heading, *headings]
    
    Path(f"data/test").mkdir(exist_ok=True, parents=True)
    subchapters = {}
    if headings[0] == chapter_titles[file.stem]:
        headings[0] = ""
    for file_number, (title, file_content) in enumerate(zip(headings, split)):
        file_name = get_file_name(title)
        subchapters[file_number] = {}
        articles = split_articles(file_content)
        subchapters[file_number]["articles"] = articles
        subchapters[file_number]["heading"] = title

    chapter = {
        "number": int(file.stem),
        "title": chapter_titles[file.stem],
        "subchapters": subchapters
    }
    chapters.append(chapter)
chapters = sorted(chapters, key=lambda x: x["number"])
with open(f"data/test/constitution.json", "wt") as f:
    json.dump({"chapters": chapters}, f, ensure_ascii=False, indent=4)

In [2]:
import json
with open("konstytucja-rag/data/test/constitution.json") as f:
    constitution = json.load(f)
constitution

{'chapters': [{'number': 0,
   'title': 'PREAMBUŁA',
   'subchapters': {'0': {'articles': {'-1': 'W trosce o byt i przyszłość naszej Ojczyzny,  \n  \nodzyskawszy w 1989 roku możliwość suwerennego i demokratycznego stanowienia o\nJej losie,  \n  \nmy, Naród Polski - wszyscy obywatele Rzeczypospolitej,  \n  \nzarówno wierzący w Boga  \n  \nbędącego źródłem prawdy, sprawiedliwości, dobra i piękna,  \n  \njak i nie podzielający tej wiary,  \n  \na te uniwersalne wartości wywodzący z innych źródeł,  \n  \nrówni w prawach i w powinnościach wobec dobra wspólnego - Polski,  \n  \nwdzięczni naszym przodkom za ich pracę, za walkę o niepodległość okupioną\nogromnymi ofiarami, za kulturę zakorzenioną w chrześcijańskim dziedzictwie\nNarodu i ogólnoludzkich wartościach,  \n  \nnawiązując do najlepszych tradycji Pierwszej i Drugiej Rzeczypospolitej,  \n  \nzobowiązani, by przekazać przyszłym pokoleniom wszystko, co cenne z ponad\ntysiącletniego dorobku,  \n  \nzłączeni więzami wspólnoty z naszymi rod

In [61]:
import json
with open("konstytucja-rag/data/test/constitution.json") as f:
    constitution = json.load(f)

print(constitution)

from langchain_core.documents import Document
documents = [
    Document(
        page_content=f"Artykuł {article_number}\n\n{article_content}",
        metadata={"chapter_number": chapter["number"], "chapter_title": chapter["title"],
                  "subchapter_title": subchapter["heading"], "subchapter_number": subchapter_number,
                  "article_number": article_number},
    )
    for chapter in constitution["chapters"]
    for subchapter_number, subchapter in chapter["subchapters"].items()
    for article_number, article_content in subchapter["articles"].items()
]

{'chapters': [{'number': 0, 'title': 'PREAMBUŁA', 'subchapters': {'0': {'articles': {'-1': 'W trosce o byt i przyszłość naszej Ojczyzny,  \n  \nodzyskawszy w 1989 roku możliwość suwerennego i demokratycznego stanowienia o\nJej losie,  \n  \nmy, Naród Polski - wszyscy obywatele Rzeczypospolitej,  \n  \nzarówno wierzący w Boga  \n  \nbędącego źródłem prawdy, sprawiedliwości, dobra i piękna,  \n  \njak i nie podzielający tej wiary,  \n  \na te uniwersalne wartości wywodzący z innych źródeł,  \n  \nrówni w prawach i w powinnościach wobec dobra wspólnego - Polski,  \n  \nwdzięczni naszym przodkom za ich pracę, za walkę o niepodległość okupioną\nogromnymi ofiarami, za kulturę zakorzenioną w chrześcijańskim dziedzictwie\nNarodu i ogólnoludzkich wartościach,  \n  \nnawiązując do najlepszych tradycji Pierwszej i Drugiej Rzeczypospolitej,  \n  \nzobowiązani, by przekazać przyszłym pokoleniom wszystko, co cenne z ponad\ntysiącletniego dorobku,  \n  \nzłączeni więzami wspólnoty z naszymi rodakami 

In [35]:
documents

[Document(page_content='Artykuł -1\n\nW trosce o byt i przyszłość naszej Ojczyzny,  \n  \nodzyskawszy w 1989 roku możliwość suwerennego i demokratycznego stanowienia o\nJej losie,  \n  \nmy, Naród Polski - wszyscy obywatele Rzeczypospolitej,  \n  \nzarówno wierzący w Boga  \n  \nbędącego źródłem prawdy, sprawiedliwości, dobra i piękna,  \n  \njak i nie podzielający tej wiary,  \n  \na te uniwersalne wartości wywodzący z innych źródeł,  \n  \nrówni w prawach i w powinnościach wobec dobra wspólnego - Polski,  \n  \nwdzięczni naszym przodkom za ich pracę, za walkę o niepodległość okupioną\nogromnymi ofiarami, za kulturę zakorzenioną w chrześcijańskim dziedzictwie\nNarodu i ogólnoludzkich wartościach,  \n  \nnawiązując do najlepszych tradycji Pierwszej i Drugiej Rzeczypospolitej,  \n  \nzobowiązani, by przekazać przyszłym pokoleniom wszystko, co cenne z ponad\ntysiącletniego dorobku,  \n  \nzłączeni więzami wspólnoty z naszymi rodakami rozsianymi po świecie,  \n  \nświadomi potrzeby współp

In [36]:
from langchain_chroma import Chroma
from langchain_community.embeddings import HuggingFaceEmbeddings
embeddings = HuggingFaceEmbeddings(model_name="ipipan/silver-retriever-base-v1")

vectorstore = Chroma.from_documents(documents=documents, embedding=embeddings)
embeddings_retriever = vectorstore.as_retriever()

/Users/szymon/projects/konstytucja-rag/env/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [37]:
def format_docs(docs):
    return "\n\n".join([
        f"Art. {doc.metadata['article_number']} {doc.page_content}"
        for doc in docs
    ])


In [38]:
embeddings_retriever

VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_chroma.vectorstores.Chroma object at 0x3e0fe2f80>)

In [42]:
from langchain_community.retrievers import BM25Retriever
from langchain.retrievers import EnsembleRetriever
from langchain_core.runnables import (
    RunnableLambda
)
bm25_retriever = BM25Retriever.from_documents(documents)
formatter = RunnableLambda(lambda x: f"Pytanie: {x}")

formatting_retriever = formatter | embeddings_retriever

ensemble_retriever = EnsembleRetriever(
    retrievers=[bm25_retriever, formatting_retriever], weights=[0.5, 0.5]
)

In [53]:
ensemble_retriever.invoke("Co jest w artykule 3?")

[Document(page_content='Artykuł 84\n\nKażdy jest obowiązany do ponoszenia ciężarów i świadczeń publicznych, w tym\npodatków, określonych w ustawie.', metadata={'chapter_number': 2, 'chapter_title': 'WOLNOŚCI, PRAWA I OBOWIĄZKI CZŁOWIEKA I OBYWATELA', 'subchapter_title': 'OBOWIĄZKI', 'subchapter_number': '5', 'article_number': '84'}),
 Document(page_content='Artykuł 3\n\nRzeczpospolita Polska jest państwem jednolitym.', metadata={'article_number': '3', 'chapter_number': 1, 'chapter_title': 'RZECZPOSPOLITA', 'subchapter_number': '0', 'subchapter_title': ''}),
 Document(page_content='Artykuł 210\n\nRzecznik Praw Obywatelskich jest w swojej działalności niezawisły, niezależny\nod innych organów państwowych i odpowiada jedynie przed Sejmem na zasadach\nokreślonych w ustawie.', metadata={'chapter_number': 9, 'chapter_title': 'ORGANY KONTROLI PAŃSTWOWEJ  I OCHRONY PRAWA', 'subchapter_title': 'RZECZNIK PRAW OBYWATELSKICH', 'subchapter_number': '1', 'article_number': '210'}),
 Document(page_con

In [69]:
def format_for_search(chapter, subchapter, article_number, article_content):
    subchapter_name = subchapter["heading"]
    if subchapter_name != "":
        subchapter_name = f"\n{subchapter_name}\n"

    if article_number == "-1":
        article_number = ""
    else:
        article_number = f"\nArtykuł {article_number}\n"

    if chapter['number'] == 0:
        chapter_name = chapter["title"]
    else:
        chapter_name = f"Rozdział {chapter['number']} {chapter['title']}"
    chapter_name = f"{chapter_name}\n"
    return f"{article_content}\n\n\n{chapter_name}{subchapter_name}{article_number}"

In [71]:
print([
    format_for_search(chapter, subchapter, article_number, article_content)
    for chapter in constitution["chapters"]
    for subchapter_number, subchapter in chapter["subchapters"].items()
    for article_number, article_content in subchapter["articles"].items()
][1])

Rzeczpospolita Polska jest dobrem wspólnym wszystkich obywateli.


Rozdział 1 RZECZPOSPOLITA

Artykuł 1



In [26]:
def get_full_content(constitution):
    text = "KONSTYTUCJA\nRZECZYPOSPOLITEJ POLSKIEJ\n\nz dnia 2 kwietnia 1997 r.\n"
    for chapter in constitution["chapters"]:
        chapter_prefix = f"**Rozdział {chapter['number']}**\n\n" if chapter['number'] != 0 else ''
        chapter_name = f"{chapter_prefix}**{chapter['title']}**"
        text += f"\n\n{chapter_name}"
        for subchapter_number, subchapter in chapter["subchapters"].items():
            text += f"\n\n**{subchapter['heading']}**"
            for article_number, article_content in subchapter["articles"].items():
                if article_number == "-1":
                    article_prefix = ""
                else:
                    article_prefix = f"**Art. {article_number}.**\n"
                text += f"\n\n{article_prefix}{article_content}"
    return text

In [27]:
print(get_full_content(constitution))

KONSTYTUCJA
RZECZYPOSPOLITEJ POLSKIEJ

z dnia 2 kwietnia 1997 r.


**PREAMBUŁA**

****

W trosce o byt i przyszłość naszej Ojczyzny,  
  
odzyskawszy w 1989 roku możliwość suwerennego i demokratycznego stanowienia o
Jej losie,  
  
my, Naród Polski - wszyscy obywatele Rzeczypospolitej,  
  
zarówno wierzący w Boga  
  
będącego źródłem prawdy, sprawiedliwości, dobra i piękna,  
  
jak i nie podzielający tej wiary,  
  
a te uniwersalne wartości wywodzący z innych źródeł,  
  
równi w prawach i w powinnościach wobec dobra wspólnego - Polski,  
  
wdzięczni naszym przodkom za ich pracę, za walkę o niepodległość okupioną
ogromnymi ofiarami, za kulturę zakorzenioną w chrześcijańskim dziedzictwie
Narodu i ogólnoludzkich wartościach,  
  
nawiązując do najlepszych tradycji Pierwszej i Drugiej Rzeczypospolitej,  
  
zobowiązani, by przekazać przyszłym pokoleniom wszystko, co cenne z ponad
tysiącletniego dorobku,  
  
złączeni więzami wspólnoty z naszymi rodakami rozsianymi po świecie,  
  
św

KONSTYTUCJA
RZECZYPOSPOLITEJ POLSKIEJ

z dnia 2 kwietnia 1997 r.


PREAMBUŁA



Art. -1. W trosce o byt i przyszłość naszej Ojczyzny,  
  
odzyskawszy w 1989 roku możliwość suwerennego i demokratycznego stanowienia o
Jej losie,  
  
my, Naród Polski - wszyscy obywatele Rzeczypospolitej,  
  
zarówno wierzący w Boga  
  
będącego źródłem prawdy, sprawiedliwości, dobra i piękna,  
  
jak i nie podzielający tej wiary,  
  
a te uniwersalne wartości wywodzący z innych źródeł,  
  
równi w prawach i w powinnościach wobec dobra wspólnego - Polski,  
  
wdzięczni naszym przodkom za ich pracę, za walkę o niepodległość okupioną
ogromnymi ofiarami, za kulturę zakorzenioną w chrześcijańskim dziedzictwie
Narodu i ogólnoludzkich wartościach,  
  
nawiązując do najlepszych tradycji Pierwszej i Drugiej Rzeczypospolitej,  
  
zobowiązani, by przekazać przyszłym pokoleniom wszystko, co cenne z ponad
tysiącletniego dorobku,  
  
złączeni więzami wspólnoty z naszymi rodakami rozsianymi po świecie,  
  
ś